In [13]:
from srai.loaders import OSMOnlineLoader, OSMPbfLoader
from srai.loaders.osm_loaders.filters import HEX2VEC_FILTER
from srai.regionalizers import geocode_to_region_gdf
from srai.joiners import IntersectionJoiner
from srai.embedders import Hex2VecEmbedder
from srai.regionalizers import H3Regionalizer
from srai.neighbourhoods import H3Neighbourhood

## Prepare data

In [3]:
bikes_filter = {"amenity": "bicycle_rental"}

In [4]:
area = geocode_to_region_gdf("Switzerland")

In [5]:
loader = OSMOnlineLoader()
stations = loader.load(area, bikes_filter)

In [6]:
stations.explore()

In [7]:
train_city = geocode_to_region_gdf("Zurich, Switzerland")

In [8]:
loader_pbf = OSMPbfLoader()
train_features = loader_pbf.load(train_city, HEX2VEC_FILTER)

[Zurich, District Zurich, Zurich, Switzerland] Counting pbf features: 998527it [00:02, 342757.95it/s]
[Zurich, District Zurich, Zurich, Switzerland] Parsing pbf file #1: 100%|██████████| 998527/998527 [01:13<00:00, 13580.82it/s]


In [9]:
train_features

geometry aeroway  \
feature_id                                                                     
node/28137648                               POINT (8.51913 47.38881)     NaN   
node/29383266                               POINT (8.54155 47.37905)     NaN   
node/30065829                               POINT (8.50953 47.41016)     NaN   
node/30883051                               POINT (8.53542 47.37573)     NaN   
node/39947904                               POINT (8.54216 47.37673)     NaN   
...                                                              ...     ...   
relation/15844334  MULTIPOLYGON (((8.49748 47.38736, 8.49749 47.3...     NaN   
relation/15858925  MULTIPOLYGON (((8.51456 47.38942, 8.51475 47.3...     NaN   
relation/1598599   MULTIPOLYGON (((8.23557 47.50528, 8.23575 47.5...     NaN   
relation/4498952   MULTIPOLYGON (((8.44331 47.42424, 8.44346 47.4...     NaN   
relation/5967234   MULTIPOLYGON (((8.55058 47.40981, 8.55058 47.4...     NaN   

                           amenity building healthcare historic landuse  \
feature_id                                                                
node/28137648              theatre      NaN        NaN      NaN     NaN   
node/29383266       ferry_terminal      NaN        NaN      NaN     NaN   
node/30065829      bicycle_parking      NaN        NaN      NaN     NaN   
node/30883051              parking      NaN        NaN      NaN     NaN   
node/39947904                  NaN      NaN        NaN      NaN     NaN   
...                            ...      ...        ...      ...     ...   
relation/15844334              NaN      yes        NaN      NaN     NaN   
relation/15858925              NaN      yes        NaN      NaN     NaN   
relation/1598599               NaN      NaN        NaN      NaN     NaN   
relation/4498952               NaN      NaN        NaN      NaN  forest   
relation/5967234               NaN      NaN        NaN      NaN     NaN   

                  leisure military natural office         shop    sport  \
feature_id                                                                
node/28137648         NaN      NaN     NaN    NaN          NaN      NaN   
node/29383266         NaN      NaN     NaN    NaN          NaN      NaN   
node/30065829         NaN      NaN     NaN    NaN          NaN      NaN   
node/30883051         NaN      NaN     NaN    NaN          NaN      NaN   
node/39947904         NaN      NaN     NaN    NaN  supermarket      NaN   
...                   ...      ...     ...    ...          ...      ...   
relation/15844334     NaN      NaN     NaN    NaN          NaN      NaN   
relation/15858925     NaN      NaN     NaN    NaN          NaN      NaN   
relation/1598599      NaN      NaN   water    NaN          NaN      NaN   
relation/4498952      NaN      NaN     NaN    NaN          NaN      NaN   
relation/5967234    track      NaN     NaN    NaN          NaN  cycling   

                  tourism  water waterway  
feature_id                                 
node/28137648         NaN    NaN      NaN  
node/29383266         NaN    NaN      NaN  
node/30065829         NaN    NaN      NaN  
node/30883051         NaN    NaN      NaN  
node/39947904         NaN    NaN      NaN  
...                   ...    ...      ...  
relation/15844334     NaN    NaN      NaN  
relation/15858925     NaN    NaN      NaN  
relation/1598599      NaN  river      NaN  
relation/4498952      NaN    NaN      NaN  
relation/5967234      NaN    NaN      NaN  

[84986 rows x 16 columns]

In [10]:
train_regions = H3Regionalizer(resolution=10).transform(train_city)
train_regions.explore()

In [11]:
joiner = IntersectionJoiner()

train_joint = joiner.transform(train_regions, train_features)

In [14]:
embedder = Hex2VecEmbedder(encoder_sizes=[21, 37])
neighbourhood = H3Neighbourhood(train_regions)

In [15]:
train_embeddings = embedder.fit_transform(train_regions, train_features, train_joint, neighbourhood, trainer_kwargs={"max_epochs": 3})

100%|██████████| 6641/6641 [00:00<00:00, 31843.69it/s]
/home/piotr/projects/srai-tutorial/.venv/lib/python3.11/site-packages/torch/cuda/__init__.py:546: UserWarning: Can't initialize NVML
  warnings.warn("Can't initialize NVML")
GPU available: False, used: False
TPU available: False, using: 0 TPU cores
IPU available: False, using: 0 IPUs
HPU available: False, using: 0 HPUs
/home/piotr/projects/srai-tutorial/.venv/lib/python3.11/site-packages/pytorch_lightning/trainer/connectors/logger_connector/logger_connector.py:67: UserWarning: Starting from v1.9.0, `tensorboardX` has been removed as a dependency of the `pytorch_lightning` package, due to potential conflicts with other packages in the ML ecosystem. For this reason, `logger=True` will use `CSVLogger` as the default logger, unless the `tensorboard` or `tensorboardX` packages are found. Please `pip install lightning[extra]` or one of them to enable TensorBoard support by default
  warning_cache.warn(
/home/piotr/projects/srai-tutorial/

Epoch 2: 100%|██████████| 1218/1218 [00:13<00:00, 93.55it/s, v_num=0] 

`Trainer.fit` stopped: `max_epochs=3` reached.


Epoch 2: 100%|██████████| 1218/1218 [00:13<00:00, 93.50it/s, v_num=0]


In [59]:
from sklearn.svm import SVC
from sklearn.model_selection import train_test_split

In [24]:
bikes_joint = joiner.transform(train_regions, stations)

In [29]:
train_regions.explore()

In [37]:
positive_samples = train_regions.join(bikes_joint)
positive_samples = positive_samples.reset_index().drop(columns=["feature_id"]).set_index("region_id")
len(positive_samples)

163

In [39]:
train_data = train_embeddings.copy()

In [41]:
train_data["target"] = 0
train_data.loc[positive_samples.index, "target"] = 1

In [60]:
regressor = SVC()

In [61]:
X = train_data.copy().drop(columns=["target"])
y = train_data.copy()["target"]

In [62]:
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=42, stratify=y)

In [63]:
regressor.fit(X_train, y_train)

SVC()

In [64]:
y_preds = regressor.predict(X_test)

In [66]:
y_preds.sum()

0